In this notebook we explore "surprise" of overall data and at each race group 

In [29]:
%load_ext autoreload
%autoreload 2
%env ANYWIDGET_HMR=1
%load_ext rpy2.ipython

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
env: ANYWIDGET_HMR=1
The rpy2.ipython extension is already loaded. To reload it, use:
  %reload_ext rpy2.ipython


In [30]:
from surprise_explora import Widget

w = Widget()

# Prepare Dataframe

Get the census poverty data using R.

In [31]:
%%R -o poverty_data
#Install packages
install.packages('tidycensus')

#load packages
library(tidycensus)
library(dplyr)
library(tidyr)
library(stringr)

#Set API Key
Sys.setenv(CENSUS_KEY="f7332e69229418824c5765d1baad389fdb9b923c")

# Target variables
poverty_vars <- c(
  white_total    = "B17001A_001",  # Total White population
  white_poverty  = "B17001A_002",  # White population below poverty
  black_total    = "B17001B_001",  # Total Black population
  black_poverty  = "B17001B_002",  # Black population below poverty
  hispanic_total    = "B17001I_001",  # Total Hispanic population
  hispanic_poverty  = "B17001I_002",   # Hispanic population below poverty
  indian_total    = "B17001C_001",  # Total Indian population
  indian_poverty  = "B17001C_002",   # Indian population below poverty
  hawaiian_total    = "B17001E_001",  # Total Hawaiian population
  hawaiian_poverty  = "B17001E_002",   # Hawaiian population below poverty
  asian_total    = "B17001D_001",  # Total Asian population
  asian_poverty  = "B17001D_002",   # Asian population below poverty
  other_total    = "B17001F_001",  # Total Other population
  other_poverty  = "B17001F_002",   # Other population below poverty
  county_total = "B17001_001", # Total County Population
  county_poverty = "B17001_002" # Total County Poverty
)

# Retrieve county-level data
poverty_data <- get_acs(
  geography = "county",
  variables = poverty_vars,
  year = 2021,
  survey = "acs5",
  output    = "wide"
)
poverty_data

* installing *source* package ‘tidycensus’ ...
** package ‘tidycensus’ successfully unpacked and MD5 sums checked
** using staged installation
** R
** data
*** moving datasets to lazyload DB
** byte-compile and prepare package for lazy loading
** help
*** installing help indices
** building package indices
** testing if installed package can be loaded from temporary location
** testing if installed package can be loaded from final location
** testing if installed package keeps a record of temporary installation path
* DONE (tidycensus)


# A tibble: 3,221 × 34
   GEOID NAME            white_totalE white_totalM white_povertyE white_povertyM
   <chr> <chr>                  <dbl>        <dbl>          <dbl>          <dbl>
 1 01001 Autauga County…        43418          340           4466            916
 2 01003 Baldwin County…       190099         1450          14300           1789
 3 01005 Barbour County…        10419          246           1465            349
 4 01007 Bibb County, A…        16426          212           2132            534
 5 01009 Blount County,…        54034          627           6885           1017
 6 01011 Bullock County…         2442          406            471            376
 7 01013 Butler County,…         9661          140            933            278
 8 01015 Calhoun County…        82817          704          11853           1254
 9 01017 Chambers Count…        19543          174           2913            585
10 01019 Cherokee Count…        22611          177           3166            648
# ℹ 3

Installing package into ‘/home/hilson/R/x86_64-pc-linux-gnu-library/4.4’
(as ‘lib’ is unspecified)
trying URL 'https://cran.case.edu/src/contrib/tidycensus_1.7.1.tar.gz'
Content type 'application/x-gzip' length 2279609 bytes (2.2 MB)
downloaded 2.2 MB


The downloaded source packages are in
	‘/tmp/RtmppTDF01/downloaded_packages’
Getting data from the 2017-2021 5-year ACS


Format the data and add typology information

In [32]:
import pandas as pd

poverty_data_by_race = poverty_data.copy()

poverty_data_by_race["white_rate"]   = (poverty_data_by_race["white_povertyE"]   / poverty_data_by_race["white_totalE"])   
poverty_data_by_race["black_rate"]   = (poverty_data_by_race["black_povertyE"]   / poverty_data_by_race["black_totalE"])   
poverty_data_by_race["hispanic_rate"] = (poverty_data_by_race["hispanic_povertyE"] / poverty_data_by_race["hispanic_totalE"]) 

poverty_data_by_race["indian_rate"] = (poverty_data_by_race["indian_povertyE"] / poverty_data_by_race["indian_totalE"])
poverty_data_by_race["asian_rate"] = (poverty_data_by_race["asian_povertyE"] / poverty_data_by_race["asian_totalE"])
poverty_data_by_race["hawaiian_rate"] = (poverty_data_by_race["hawaiian_povertyE"] / poverty_data_by_race["hawaiian_totalE"]) 
poverty_data_by_race["other_rate"] = (poverty_data_by_race["other_povertyE"] / poverty_data_by_race["other_totalE"])

poverty_data_by_race["global_rate"]     = (poverty_data_by_race["county_povertyE"]  / poverty_data_by_race["county_totalE"])  

poverty_data_by_race = poverty_data_by_race.rename(columns={
    "white_totalE":    "white_pop",
    "black_totalE":    "black_pop",
    "hispanic_totalE": "hispanic_pop",
    "asian_totalE" : "asian_pop",
    "indian_totalE" : "indian_pop",
    "other_totalE" : "other_pop",
    "hawaiian_totalE" : "hawaiian_pop",
    "county_totalE":   "global_pop"
})

df = poverty_data_by_race[[
    "GEOID",                    
    "NAME",
    "black_rate",
    "black_pop",
    "white_rate",
    "white_pop",
    "hispanic_rate",
    "hispanic_pop",

    "asian_rate",
    "asian_pop",
    "indian_rate",
    "indian_pop",
    "other_rate",
    "other_pop",
    "hawaiian_rate",
    "hawaiian_pop",
    
    "global_rate",
    "global_pop"
]].rename(columns={"GEOID": "fips"})

county_typology = pd.read_csv('../data/county_typology.csv', dtype=str)

df = pd.merge(df, county_typology, on='fips', how='left').dropna()

df['state'] = df['NAME'].str.split(', ').str[1].str.strip()
df["name"] = df["NAME"].str.split(", ").str[0]


In [33]:
df

fips                        NAME  black_rate  black_pop  white_rate  \
1     01003     Baldwin County, Alabama    0.205767    19109.0    0.075224   
2     01005     Barbour County, Alabama    0.361528    10262.0    0.140609   
4     01009      Blount County, Alabama    0.233494      621.0    0.127420   
7     01015     Calhoun County, Alabama    0.263768    24078.0    0.143123   
8     01017    Chambers County, Alabama    0.158684    13801.0    0.149056   
...     ...                         ...         ...        ...         ...   
3130  56021     Laramie County, Wyoming    0.354425     2260.0    0.082090   
3132  56025     Natrona County, Wyoming    0.387454      542.0    0.096317   
3138  56037  Sweetwater County, Wyoming    0.196281      484.0    0.101840   
3139  56039       Teton County, Wyoming    0.174699      166.0    0.060213   
3142  56045      Weston County, Wyoming    1.000000       16.0    0.136818   

      white_pop  hispanic_rate  hispanic_pop  asian_rate  asian_pop  ...  \
1      190099.0       0.183290       10066.0    0.113563     2175.0  ...   
2       10419.0       0.603568        1009.0    0.000000      100.0  ...   
4       54034.0       0.258082        5599.0    0.032407      216.0  ...   
7       82817.0       0.254446        4555.0    0.110218      871.0  ...   
8       19543.0       0.410944         932.0    0.178771      358.0  ...   
...         ...            ...           ...         ...        ...  ...   
3130    84529.0       0.173709       14910.0    0.147032     1095.0  ...   
3132    71680.0       0.156747        6922.0    0.101333      375.0  ...   
3138    36410.0       0.171037        6788.0    0.185031      481.0  ...   
3139    19813.0       0.114976        3479.0    0.178862      369.0  ...   
3142     5796.0       0.358974          78.0    0.000000       50.0  ...   

      indian_pop  other_rate  other_pop  hawaiian_rate  hawaiian_pop  \
1         1159.0    0.200797     3765.0       0.000000           9.0   
2           23.0    0.505297      944.0       1.000000           1.0   
4          189.0    0.347967     1230.0       0.000000          74.0   
7          256.0    0.298942     1890.0       0.000000         168.0   
8           55.0    0.005495      182.0       0.000000           3.0   
...          ...         ...        ...            ...           ...   
3130       918.0    0.169271     3072.0       0.105263          57.0   
3132       711.0    0.098916      738.0       0.000000          30.0   
3138       502.0    0.200683     1171.0       0.000000          41.0   
3139        24.0    0.166133     2185.0       0.000000          15.0   
3142        86.0    0.000000        7.0       0.000000          70.0   

      global_rate  global_pop                typology    state  \
1        0.092049    223772.0    Rural Middle America  Alabama   
2        0.264719     22250.0  African American South  Alabama   
4        0.132366     58323.0        Evangelical Hubs  Alabama   
7        0.175384    113294.0   Working Class Country  Alabama   
8        0.150713     34350.0  African American South  Alabama   
...           ...         ...                     ...      ...   
3130     0.090179     97861.0                  Exurbs  Wyoming   
3132     0.098777     77680.0    Rural Middle America  Wyoming   
3138     0.104814     41941.0                  Exurbs  Wyoming   
3139     0.071170     23240.0                  Exurbs  Wyoming   
3142     0.140856      6496.0         Aging Farmlands  Wyoming   

                   name  
1        Baldwin County  
2        Barbour County  
4         Blount County  
7        Calhoun County  
8       Chambers County  
...                 ...  
3130     Laramie County  
3132     Natrona County  
3138  Sweetwater County  
3139       Teton County  
3142      Weston County  

[1542 rows x 21 columns]

# Setup Surprise

Filter out only the counties we are interested in.

Then we create surprise object by adding groups we are interested in.

We then calculate surprise only for the filtered counties and the groups.

In [34]:
# Filter out an individual county
county_list = ["06037"]
df_filtered = df[~df["fips"].isin(county_list)]

# Filter by population range
df_filtered = df[(df["global_pop"] > 100000) & (df["global_pop"] < 200000)]
# df_filtered = surprise.df[(surprise.df['white_pop'] > 100000) & (surprise.df['white_pop'] < 200000)]
# df_filtered = surprise.df[(surprise.df['black_pop'] > 100000) & (surprise.df['black_pop'] < 200000)]
# df_filtered = surprise.df[(surprise.df['hispanic_pop'] > 100000) & (surprise.df['hispanic_pop'] < 200000)]

# Filter by typology - comment out typology
typology = [
    "Working Class Country",
    "Rural Middle America",
    "African American South",
    #'Evangelical Hubs'
    #'Military Posts',
    #'College Towns',
    #'Exurbs',
    #'Native American Lands',
    #'Graying America',
    #'Hispanic Centers',
    #'Big Cities',
    #'Urban Suburbs',
    #'Aging Farmlands',
    #'Middle Suburbs',
    #'LDS Enclaves',
]
df_filtered = df[df["typology"].isin(typology)]

df_filtered = df_filtered.copy()

In [35]:
from surprise_explora import Surprise

groups = ['white', 'black', 'hispanic', 'asian', 'indian', 'hawaiian', 'other']
rate_keys = ['white_rate', 'black_rate', 'hispanic_rate', 'asian_rate', 'indian_rate', 'hawaiian_rate', 'other_rate']
population_keys = ['white_pop', 'black_pop', 'hispanic_pop', 'asian_pop', 'indian_pop', 'hawaiian_pop', 'other_pop']
global_rate_key = 'global_rate'
global_population_key = 'global_pop'

surprise = Surprise(
    df=df_filtered,
    groups=groups, 
    rate_keys=rate_keys,
    population_keys=population_keys,
    global_rate_key=global_rate_key,
    global_population_key=global_population_key
)

# Calculate surprise for each group
surprise.calculate()

# Plots

## Bar Chart

Barchart of filtered data inside a specified state.

Here, we look at surprise values of 3 race groups within the filtered counties in a state.

In [36]:
surprise.bar_chart(state='Alabama')

alt.FacetChart(...)

## Funnel Plots

### Global Funnel Plot with 95% CI

In [37]:
surprise.funnel_plot('global')

alt.LayerChart(...)

### White race group Funnel Plot with 95% CI

In [38]:
surprise.funnel_plot('white')

alt.LayerChart(...)

### Black race group Funnel Plot with 95% CI

In [39]:
surprise.funnel_plot('black')

alt.LayerChart(...)

### Hispanic race group Funnel Plot with 95% CI

In [40]:
surprise.funnel_plot('hispanic')

alt.LayerChart(...)

### Asian race group Funnel Plot with 95% CI

In [41]:
surprise.funnel_plot('asian')

alt.LayerChart(...)

### Indian race group Funnel Plot with 95% CI

In [42]:
surprise.funnel_plot('indian')

alt.LayerChart(...)

### Hawaiian race group Funnel Plot with 95% CI

In [43]:
surprise.funnel_plot('hawaiian')

alt.LayerChart(...)

### Other race group Funnel Plot with 95% CI

In [44]:
surprise.funnel_plot('other')

alt.LayerChart(...)